# Tutorial for UAIQM in MLatom@XACS

## Introduction to UAIQM methods

**UAIQM** (**universal and updatable AI-enhanced quantum mechanical methods**) hosts a library of foundational methods ranging from pure machine learning methods to hybrid machine learning/quantum mechanical methods, which can be used out-of-box without retraining while maintaining both high accuracy and low computational cost.

We also provide auto-selection utility for choosing the optimal UAIQM method and self-improvement procedure (will come soon) for constant library updating with more usage.

## Outline of this tutorial

This tutorial will be arranged as follows:
Firstly we will illustrate **how to use separate UAIQM method via MLatom to perform various tasks**.
Then, **automatic selection procedure** is introduced for optimal selection of UAIQM methods given expected time budget and input chemical system.  

- 1 - Using UAIQM methods with MLatom
    - 1.0 - Define a UAIQM Method
    - 1.1 - Single-point Calculations
    - 1.2 - Geometry Optimization
    - 1.3 - Frequencies and thermochemistry
- 2 - Automatic selection of UAIQM methods
    - 2.0 - Usage of Auto-selection Utility
    - 2.1 - Reaction Energies for Diels-Alder Reaction
    - 2.2 - Quasiclassical Trajectories Analysis on the Bifurcating Pericyclic Reaction

## 1 - Using UAIQM methods with MLatom

First, we will import some necessary modules

In [22]:
# import mlatom
import mlatom as ml 

In [23]:
# load mkl
import os, re, subprocess
if not 'MODULEPATH' in os.environ:
        f = open(os.environ['MODULESHOME'] + "/init/.modulespath", "r")
        path = []
        for line in f.readlines():
                line = re.sub("#.*$", '', line)
                if line is not '':
                        path.append(line)
        os.environ['MODULEPATH'] = ':'.join(path)
if not 'LOADEDMODULES' in os.environ:
        os.environ['LOADEDMODULES'] = ''
def module(*args):
        if type(args[0]) == type([]):
            args = args[0]
        else:
            args = list(args)
        (output, error) = subprocess.Popen(['/usr/bin/modulecmd', 'python'] +args, stdout=subprocess.PIPE).communicate()
        exec(output)
module("load", "mkl")

Loading mkl version 2023.0.0


### 1.0 - Define a UAIQM method

Similar to other methods defined in MLatom, user just need to specify the method name and version of the method with `ml.models.methods` module

In [ ]:
uaiqm = ml.models.methods(method='uaiqm_gfn2xtbstar@cc', version='newest') # latest version
# uaiqm = ml.models.methods(method='uaiqm_gfn2xtbstar@cc') # latest version
# uaiqm = ml.models.methods(method='uaiqm_gfn2xtbstar@cc', version='20240106') # user specified version

By default, the newest version of the method choosed will be used if `version` keyword is not set. If uesr wants to specify specific keywords for each component to UAIQM method, `baseline_kwargs`, and `dispersion_kwargs` can be used. For example, for DFT-based UAIQM method, if user want to set threads used for baseline DFT, method can be defined as:

In [ ]:
uaiqm = ml.models.methods(method='uaiqm_wb97xdef2tzvpp@cc', version='newest', baseline_kwargs={'nthreads':18})

**NOTE**: We use PySCF for DFT, modified xTB for GFN2-xTB*, Sparrow for ODM2* and dftd4 for d4 dispersion correction in UAIQM methods. By default all the CPUs available will be used.

### 1.1 - Single-point Calculations

In [16]:
# define UAIQM method
uaiqm = ml.models.methods(method='uaiqm_gfn2xtbstar@cc', version='newest')

In [17]:
# load molecule
mol = ml.data.molecule.from_xyz_string('''5

C         0.0000000000        0.0000000000        0.0000000000
H         1.0870000000        0.0000000000        0.0000000000
H        -0.3623333220       -1.0248334322       -0.0000000000
H        -0.3623333220        0.5124167161       -0.8875317869
H        -0.3623333220        0.5124167161        0.8875317869
''')

In [18]:
# perform single point calculations
uaiqm.predict(
    molecule=mol, 
    calculate_energy=True,
    calculate_energy_gradients=True,
    calculate_hessian=True)

In [ ]:
print(f'Standard deviation of ML contribution: {mol.energy_standard_deviation:.6f} Hartree ' \
    + f'{mol.energy_standard_deviation * ml.constants.Hartree2kcalpermol:.6f} kcal/mol')
print(f'Baseline contribution: {mol.baseline_energy:.6f} Hartree')
print(f'NN contribution: {mol.MLs_energy:.6f} Hartree')
print(f'D4 contribution: {mol.dispersion_energy:.6f} Hartree')
print(f'Total energy: {mol.energy:.6f} Hartree')

print('\nGradients for molecule:')
print(mol.get_energy_gradients())

print('\nHessian for molecule:')
print(mol.hessian)

### 1.2 - Geometry Optimization 

In [ ]:
# define UAIQM method
uaiqm = ml.models.methods(method='uaiqm_gfn2xtbstar@cc', version='newest')

In [ ]:
# load initial molecule
initmol = ml.data.molecule.from_xyz_string('''5

C         0.0000000000        0.0000000000        0.0000000000
H         1.0870000000        0.0000000000        0.0000000000
H        -0.3623333220       -1.0248334322       -0.0000000000
H        -0.3623333220        0.5124167161       -0.8875317869
H        -0.3623333220        0.5124167161        0.8875317869
''')

In [ ]:
# perform geometry optimization
geomopt = ml.geometry_optimization(
    model=uaiqm,
    initial_molecule=initmol,
)

In [ ]:
# Get the final geometry
final_mol = geomopt.optimized_molecule
# and its XYZ coordinates
final_mol.xyz_coordinates

# save the final geometry
final_mol.write_file_with_xyz_coordinates(filename='final.xyz')

### 1.3 - Frequencies and Thermochemistry
we will use previously optimized methane to perform frequency calcuation and get thermochemical properties.

In [ ]:
# perform frequency calculations
freq = ml.thermochemistry(model=uaiqm, molecule=final_mol)

In [ ]:
# Save the molecule with vibration analysis and thermochemistry results
final_mol.dump(filename='final_mol.json',format='json')

In [ ]:
# Check vibration analysis
print("Mode     Frequencies     Reduced masses     Force Constants")
print("           (cm^-1)            (AMU)           (mDyne/A)")
for ii in range(len(final_mol.frequencies)):
    print("%d   %13.4f   %13.4f   %13.4f"%(ii,final_mol.frequencies[ii],final_mol.reduced_masses[ii],final_mol.force_constants[ii]))

# Check thermochemistry results
print(f"Zero-point vibrational energy: {final_mol.ZPE} Hartree")
print(f"Enthalpy at 298 K: {final_mol.H} Hartree")
print(f"Gibbs Free energy at 298 K: {final_mol.G} Hartree")
print(f"Heat of formation at 298 K: {final_mol.DeltaHf298} Hartree")

## 2 - Automatic selection of UAIQM methods
With atomatic selection, UAIQM library provides user with the optmial method given the **chemical system**, **expected time budget** and **computational resources** (no need for online calculations). 

The uncertainty is calibrated on the standard CHNO set to obtain thresholds for certain predictions at each baseline level. If the uncertainty exceeds the threshold, the calculation will give the warning.

### 2.0 - Usage of Auto-selection Utility

To use automatic selection with MLatom, users need to use `mlatom.models.uaiqm()` module and choose `method="uaiqm_optimal"`. Then the select function `selection_optimal()` can be used to choose the optimal method. User need to provide three options as have mentioned in the workflow above:

- `molecule (mlatom.data.molecule)`: the input molecule
- `nCPUs (int)`: the number of CPU used.
- `time_budget (str)`: the expected time used. `s`, `m`, `h` and `d` can be recognized, e.g. `3m`.

A simple example to perform single point calculation is provided:

In [ ]:
import mlatom as ml

mol = ml.data.molecule.from_xyz_string('''5

C         0.0000000000        0.0000000000        0.0000000000
H         1.0870000000        0.0000000000        0.0000000000
H        -0.3623333220       -1.0248334322       -0.0000000000
H        -0.3623333220        0.5124167161       -0.8875317869
H        -0.3623333220        0.5124167161        0.8875317869
''')

uaiqm_optimal = ml.models.uaiqm(method='uaiqm_optimal', verbose=True)
# verbose = True in the above line requests to print the information about the model
uaiqm_optimal.select_optimal(
    molecule=mol,
    nCPUs=1,
    time_budget='1s'
)
uaiqm_optimal.predict(molecule=mol, calculate_energy=True)
print(mol.energy)

### 2.1 - Reaction Energies for Diels-Alder Reaction
We prepared DARC dataset in json format from GMTKN55 which can be downloaded in our tutorial https://xacs.xmu.edu.cn/docs/mlatom/tutorial_uaiqm.html. We will try cheap and accurate UAIQM method at time budget 0.1s. 
The final results will be written to `reaction_summary` and `molecule_summary` where the prediction of reaction energies, UAIQM method used for each molecule and their uncertainty are stored. If `verbose=True`, then information for each selection step will be reported.

In [ ]:
import mlatom as ml

In [ ]:
# load reaction dataset
darc = ml.data.reactions_database()
darc.load(f'DARC.json', format='json')

In [ ]:
# perform calculation with uaiqm methods
darc_uaiqm = ml.data.reactions_database()
for reaction in darc.reactions:
    for mol in reaction.molecules:
        # initialize uaiqm optimal method
        uaiqm_optimal = ml.models.uaiqm(method='uaiqm_optimal', verbose=False) # set verbose to True to get the report for each selection step
        uaiqm_optimal.select_optimal(
            molecule=mol,
            nCPUs=1,
            time_budget='1s'
        )
        uaiqm_optimal.predict(molecule=mol, calculate_energy=True)
        mol.uaiqm_method = uaiqm_optimal.method
    reaction.absolute_energy()
    darc_uaiqm.reactions.append(reaction)

# write darc_uaiqm to MLatom format json file
darc_uaiqm.dump(f'DARC_with_UAIQM_methods.json', format='json')

In [ ]:
# write results to reaction_summary and molecule_summary
molecule_summary = open(f'molecule_summary', 'w')
molecule_summary.write('mol\tpred\tuaiqm_method\tUQ\n')
reaction_summary = open(f'reaction_summary', 'w')
reaction_summary.write('reaction\tref\tpred\n')

for reaction in darc_uaiqm.reactions:
    print(reaction.chemical_label)
    reaction_summary.write(f'{reaction.chemical_label}\t{reaction.ref}\t{reaction.energy*ml.constants.Hartree2kcalpermol}\n')
    for mol in reaction.molecules:
        molecule_summary.write(f'{mol.chemical_label}\t{mol.energy*ml.constants.Hartree2kcalpermol}\t{mol.uaiqm_method}\t{mol.energy_standard_deviation*ml.constants.Hartree2kcalpermol}\n')
reaction_summary.close()
molecule_summary.close()

In [ ]:
# get MAE for DARC datasets
import pandas as pd
darc_summary = pd.read_csv(f'reaction_summary', sep='\t')
mae = abs(darc_summary['pred']-darc_summary['ref']).mean()
print(f'MAE for DARC datasets: {mae} kcal/mol\n')

### 2.2 - Quasi-classical Trajectories Analysis on the Bifurcating Pericyclic Reaction

In this section, we will reproduce the quasiclassical trajectories for bifurcating pericyclic reaction reported in *JACS* (**2017**) 139,8251, where they manually choosed B3LYP-D3/6-31G* level of theory and got the distribution of the products with the resulting 117 reactive trajectories. With UAIQM methods, we can quickly shoot 1000 trajectories and get hundreds reactive ones, while the energy profile is more accurate than B3LYP which is known for low reliability on energy prediction

Below we provide instructions on the procedure to propagate one trajectory with our UAIQM methods. The required transition state geometry for generation of initial conditions can be downloaded on our tutorial website https://xacs.xmu.edu.cn/docs/mlatom/tutorial_uaiqm.html (We also provide explicitly here as string). Time budget is reduced to 0.1 s for UAIQM method. The same setting for quasi-classical MD will be used as that in the original paper, i.e. 500 fs long trajectory with 1 fs time step starting from region near ambimodal transition state. 

**NOTE**: To run 1000 trajectories, we can use slurm submission scripts and they are provided under `jupyter_examples/uaiqm/slurm` folder on xacs cloud. You can try to submit the job with command `sbatch ambimodal.sh`

In [ ]:
import mlatom as ml

In [ ]:
# load initial transitiona state
init_ts1 = ml.data.molecule.from_xyz_string('''32

C -1.73655 0.90008 0.18271
C -1.02608 0.83877 -1.14114
C -1.01999 1.05389 1.43154
C 0.08653 1.69934 -1.47134
C 0.26098 1.54795 1.66322
C 1.08110 2.16567 -0.64431
C 1.21066 2.01363 0.75521
O -2.94833 0.64245 0.17805
H 0.18669 1.93971 -2.52895
H 1.88401 2.72026 -1.12893
H 2.13801 2.38605 1.18649
H 0.56299 1.57821 2.70960
C -0.44114 -1.66332 0.99996
H -1.65054 0.85710 2.29424
C -0.52580 -0.99222 -1.23666
H -1.78094 0.82031 -1.92593
C 0.40932 -1.20338 -0.07777
C -1.72552 -1.70133 -0.88398
H -0.15259 -1.03363 -2.25558
C -1.67904 -2.03540 0.47267
H -0.12666 -1.81645 2.02301
H -2.58230 -1.82716 -1.53354
H -2.49836 -2.46095 1.03963
C 1.75778 -1.02993 -0.06102
C 2.59624 -1.30352 1.16016
C 2.54815 -0.68554 -1.29546
H 1.93116 -0.28290 -2.09981
H 3.06091 -1.58290 -1.67294
H 3.32646 0.05119 -1.06623
H 2.00522 -1.49549 2.05720
H 3.25334 -0.44950 1.36358
H 3.24936 -2.17178 0.99084
''')

In [ ]:
# choose optimal UAIQM method
uaiqm_optimal = ml.models.uaiqm(method='uaiqm_optimal', verbose=False)
uaiqm_optimal.select_optimal(
    molecule=init_ts1,
    nCPUs=1,
    time_budget='0.1s'
)

In [ ]:
# optimize geometry and get frequencies
geomopt = ml.optimize_geometry(
    model=uaiqm_optimal,
    initial_molecule=init_ts1,
    ts=True,
    program='geometric'
)
optmol_ts1 = geomopt.optimized_molecule
ml.freq(model=uaiqm_optimal, molecule=optmol_ts1)

In [ ]:
# get initial conditions
for ifreq in range(len(optmol_ts1.frequencies)):
    if optmol_ts1.frequencies[ifreq] > 0 and optmol_ts1.frequencies[ifreq] < 100:
        optmol_ts1.frequencies[ifreq] = 100

init_cond_db = ml.generate_initial_conditions(molecule=optmol_ts1,
                                            generation_method='harmonic-quantum-boltzmann',
                                            number_of_initial_conditions=1000,
                                            initial_temperature=298,
                                            use_hessian=False)
# dump forward initial conditions
init_cond_db.dump(f'TS1_incond_298.json',format='json')

# Reverse the velocities to get the backward trajectories
re_init_cond_db = init_cond_db.copy()
for mol in re_init_cond_db:
    for atom in mol:
        atom.xyz_velocities = -atom.xyz_velocities
# dump backward initial conditions
re_init_cond_db.dump(f're_TS1_incond_298.json',format='json')

In [ ]:
# propagate one forward trajectory
init_mol = init_cond_db[0]
dyn = ml.md(model=uaiqm_optimal,
            molecule_with_initial_conditions = init_mol,
            ensemble='NVE',
            time_step=1,
            maximum_propagation_time=500,
            )
traj = dyn.molecular_trajectory
traj.dump(filename=f'forward_temp298_mol0', format='plain_text')

# propagate backward trajectory
re_init_mol = re_init_cond_db[0]
dyn = ml.md(model=uaiqm_optimal,
            molecule_with_initial_conditions = re_init_mol,
            ensemble='NVE',
            time_step=1,
            maximum_propagation_time=500,
            )
traj = dyn.molecular_trajectory
traj.dump(filename=f'backward_temp298_mol0', format='plain_text')

In [ ]:
# check reactive trajectories
import numpy as np
def get_bond_data(traj_xyz, bonds):
    nmol = len(traj_xyz)
    data = np.zeros((nmol, len(bonds)))
    for ii in range(nmol):
        mol = traj_xyz[ii]
        bl_list = []
        for bond in bonds:
            bl = mol.internuclear_distance(bond[0], bond[1])
            bl_list.append(bl)
        data[ii] = bl_list
    return data

def check_reactive(traj_bond_data):
    P1 = False # C2-C15 C7-C24
    P2 = False # C2-C15 C3-C13
    for ii in range(traj_bond_data.shape[0]):
        bond_data = traj_bond_data[ii]
        if bond_data[0] <= 1.6 and bond_data[1] <= 1.6:
            P2 = True
        if bond_data[0] <= 1.6 and bond_data[2] <= 1.6:
            P1 = True

    return P1, P2

def plot(traj_data, target_path):
    ax = plt.figure().add_subplot(projection='3d')
    traj_data[traj_data>=5] = np.nan 
    ax.scatter(traj_data[:,2], traj_data[:,1], traj_data[:,0], s=1)
    ax.set_xlabel('C7-C24')
    ax.set_ylabel('C3-C13')
    ax.set_zlabel('C2-C15')
    ax.axes.set_xlim3d(left=1, right=5)
    
    ax.axes.set_ylim3d(bottom=1, top=5)
    ax.axes.set_zlim3d(bottom=1, top=5)
    ax.axes.set_yticklabels(ax.axes.get_yticklabels(),
                verticalalignment='baseline',
                horizontalalignment='left')
    ax.tick_params(axis='z', which='major', pad=1)
    ax.tick_params(axis='x', which='major', pad=1)
    #ax.grid(False) # whether to set grids in the figure
    plt.tight_layout()
    plt.savefig(target_path, dpi=150)
    
def define_components(traj_bond_data):
    P6 = False # C2-C15 C7-C24 
    P7 = False # C2-C15 C3-C13
    C2_C15 = False
    C3_C13 = False
    C7_C24 = False

    for ii in range(traj_bond_data.shape[0]):

        bond_data = traj_bond_data[ii]
        if bond_data[0] <= 1.6 and bond_data[1] <= 1.6:
            P7 = True 
        if bond_data[0] <= 1.6 and bond_data[2] <= 1.6:
            P6 = True 
        if bond_data[0] <= 1.6:
            C2_C15 = True
        if bond_data[1] <= 1.6:
            C3_C13 = True 
        if bond_data[2] <= 1.6:
            C7_C24 = True

    return P6, P7, C2_C15, C3_C13, C7_C24

In [26]:
ntrajs = 1
component_vector = np.zeros((ntrajs, 5))

bonds = [(1,14),(2,12),(6,23)]
traj_forward = ml.data.molecular_database.from_xyz_file(f'forward_temp298_mol0.xyz')
traj_backward = ml.data.molecular_database.from_xyz_file(f'backward_temp298_mol0.xyz')
traj = ml.data.molecular_database()
traj_forward.molecules.reverse()
traj.molecules = traj_forward.molecules + traj_backward.molecules
bond_data = get_bond_data(traj, bonds=bonds)
P1, P2 = check_reactive(bond_data)
component_vector[0] = define_components(bond_data)
print(f'P1 in trajectory: {P1}')
print(f'P2 in trajectory: {P2}')

In [ ]:
import matplotlib.pyplot as plt 
target_path = './traj0.png'
plot(bond_data, target_path)

## Visualization of the trajectories

In [ ]:
import py3Dmol

viewer = py3Dmol.view(width=400, height=300)
viewer.addModelsAsFrames(open(f"forward_temp298_mol0.xyz", "r").read(), 'xyz')
viewer.setStyle({"stick":{}})
viewer.zoomTo()
viewer.animate({'loop': "forward"})#, 'reps': 2, 'interval': 500})
viewer.show()